# MA School Finance Choropleth (Local Folium Viewer)
This notebook loads the preprocessed data and lets you select fiscal year and foundation enrollment range to explore Massachusetts school districts interactively.

In [2]:
import geopandas as gpd
import pandas as pd
import folium
from branca.colormap import LinearColormap

In [3]:
# Load the preprocessed file
matched_gdf = gpd.read_file('data/matched.geojson')

In [4]:
# Fiscal Year Options
years = sorted(matched_gdf['FY'].dropna().unique())
print('Available Fiscal Years:', years)

# Settings (edit these)
FY = 2025
FE_min = 0
FE_max = 10000

Available Fiscal Years: [np.int32(1993), np.int32(1994), np.int32(1995), np.int32(1996), np.int32(1997), np.int32(1998), np.int32(1999), np.int32(2000), np.int32(2001), np.int32(2002), np.int32(2003), np.int32(2004), np.int32(2005), np.int32(2006), np.int32(2007), np.int32(2008), np.int32(2009), np.int32(2010), np.int32(2011), np.int32(2012), np.int32(2013), np.int32(2014), np.int32(2015), np.int32(2016), np.int32(2017), np.int32(2018), np.int32(2019), np.int32(2020), np.int32(2021), np.int32(2022), np.int32(2023), np.int32(2024), np.int32(2025)]


In [5]:
# Filter by selected FY and FE range
filtered = matched_gdf[(matched_gdf['FY'] == FY) &
                       (matched_gdf['FE'] >= FE_min) &
                       ((matched_gdf['FE'] <= FE_max) | (FE_max == 10000))]

print(f"Filtered to {len(filtered)} rows for FY {FY} and FE {FE_min}–{FE_max}")

Filtered to 285 rows for FY 2025 and FE 0–10000


In [8]:
# Set up color scale
viridis_colors = ["#440154", "#46337F", "#365C8D", "#277F8E", "#1FA187", "#4AC16D", "#A0DA39", "#FDE725"]
colormap = LinearColormap(colors=viridis_colors[::-1], vmin=0.5, vmax=3,
                          caption="Actual Net School Spending as % of Required (e.g. 210%)")

In [10]:
# Build the Folium map
m = folium.Map(location=[42.3, -71.8], zoom_start=7, tiles='CartoDB Positron')

for _, row in filtered.iterrows():
    val = min(row['ActualNSS_portion_ReqNSS'], 3)
    color = '#e6007e' if row['ActualNSS_portion_ReqNSS'] > 3 else colormap(val)
    popup = folium.Popup(f"<b>{row['DistOrg']}</b><br>NSS: {val * 100:.0f}%", max_width=250)
    folium.GeoJson(row['geometry'],
                   style_function=lambda x, color=color: {
                       'fillColor': color,
                       'color': 'white',
                       'weight': 1,
                       'fillOpacity': 0.8
                   },
                   popup=popup).add_to(m)

colormap.add_to(m)
m.save("output/map.html")
m